#**Título** Experimento colaborativo "canarios asesinos"

## **Autor**: Stella Vilca
## **Fecha de última modificación:** 10/11/2024
## **Descripción:** pruebas aplicando la técnica de "canaritos asesinos"con distintos valores de semillas, ratios y desvios

## Parámetros
< Descripción de cada uno de los parámetros que utiliza el job >

In [ ]:
#variables a setear
training = [202101, 202102, 202103] # completar con los periodos
validation =[202104] # completar con el mes de test
undersampling_value = 0.1 # utilizado para el dataset de train de LGBM
gan1 = 273000 # utilizado para la funcion de ganancia de LGBM
gan0 = -7000 # utilizado para la funcion de ganancia de LGBM
canaritos_semilla = [191173, 371311, 644117, 998377, 800161] # completar con la semilla personal
canaritos_ratio = [1.25, 1.5, 1.75, 2, 2.25, 2.5, 2.75, 3, 3.25, 3.5, 3.75, 4] # valor con el que se multiplicara la cantidad de columnas para obtener las variables canarios
canaritos_desvios = [-2, -1, 0, 1, 2] # desvio utilizado para definir el umbral de seleccion de variables
# resultados de las pruebas
resultados = pd.DataFrame({
    'Nro',
    'Ratio',
    'Desvio',
    'Variables importantes',
    'Eliminadas',
    'Ganancia',
    'Semilla'
    })
numero = 1 # contador de pruebas
ganancia_acierto = 273000 # usado para conocer la ganancia del dataset resultante luego de la eliminacion de variables
costo_estimulo = 7000 # usado para conocer la ganancia del dataset resultante luego de la eliminacion de variables
mes_train = 202102 # mes de entrenamiento para obtener la ganancia el dataset resultante luego de la eliminacion de variables
mes_test = 202104 # mes de test para obtener la ganancia el dataset resultante luego de la eliminacion de variables
dataset_path = '/home/stellavilca/buckets/b1/datasets/'
dataset_file = 'competencia_02.csv.gz'

## Input
< Archivos de datos (csv.gz) con sus paths que van a consumirse por el job>

In [ ]:
# dataset competencia 2 con la clase ternaria calculada
dataset_path = '/home/stellavilca/buckets/b1/datasets/' #reemplzar por path correspondiente
dataset_file = 'competencia_02.csv.gz'# archivo de la competencia 02 a la que se le calculo previamente la clase ternaria


## Output

< Archivos, bases de datos, modelos que va a generar el job>

In [ ]:
#Archivo: competencia02_FS.zip
#archivo zipeado con las variables seleccionadas luego de aplicar canarios asesinos y que obtuvo la mayor ganancia entre las pruebas, se guarda al finalizar el proceso

#Archivo: resultadoscanaritos.csv
#archivo con el resultado de las pruebas realizadas, se guarda al final del proceso

#Archivo: colutiles'+xxx+'.txt', donde xxx es número de la prueba
#archivo con los nombres de las variables importantes, se guarda uno por cada prueba



### Paquetes necesarios

In [ ]:
import pandas as pd
import numpy as np
from lightgbm import Dataset, train
import lightgbm as lgb
import os

## Código del proceso

< Todo el código a partir de aquí debe poder ejecutarse sin necesidad de parametrizar nada>

In [ ]:
# Funcion de feval de lgbm
VPOS_CORTE = []
def fganancia_lgbm_meseta(probs, datos):
    vlabels = datos.get_label()
    vpesos = datos.get_weight()
    tbl = pd.DataFrame({
        "prob": probs,
        "gan": np.where((vlabels == 1) & (vpesos > 1), gan1, gan0)
    })

    tbl = tbl.sort_values(by="prob", ascending=False)
    tbl["posicion"] = np.arange(1, len(tbl) + 1)
    tbl["gan_acum"] = tbl["gan"].cumsum()
    tbl = tbl.sort_values(by="gan_acum", ascending=False)

    gan = tbl["gan_acum"].iloc[:500].mean()
    pos_meseta = tbl["posicion"].iloc[:500].median()
    VPOS_CORTE.append(pos_meseta)
    return 'ganancia', gan, True

campitos = np.unique([
    ["foto_mes"],
    ["clase_ternaria"]
])

for valorsemilla in canaritos_semilla:
  #generar variables canaritos
  for valorratio in canaritos_ratio:
    dataset = pd.read_csv(dataset_path + dataset_file,compression='gzip')
    np.random.seed(valorsemilla)
    for i in range(int(len(dataset.columns) * valorratio)):
        dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
    #crea la columna clase01, tiene 1 cuando es BAJA+1 y BAJA+2 y cero cuando continua
    dataset["clase01"] = 0
    dataset.loc[dataset["clase_ternaria"].isin(["BAJA+2", "BAJA+1"]), "clase01"] = 1
    #guardo los nombres de los campos buenos, excluyendo foto mes, clase ternaria y clase01
    campos_buenos = [col for col in dataset.columns if col not in ["foto_mes","clase_ternaria","clase01"] ]
    #crea la columna entrenamiento, tiene 1 si foto mes esta en el conjunto de meses de entrenamiento y si la
    #clase ternaria es BAJA+1 O BAJA+2 o el número generado al azar es menor al valor de undersampling
    #se usa undersampling para reducir el tiempo de proceso
    azar = np.random.uniform(0, 1, len(dataset))
    dataset['entrenamiento'] = (
      dataset['foto_mes'].isin(training) &  # Condición de pertenencia al conjunto de entrenamiento
      ((dataset['clase01'] == 1) | (azar < undersampling_value))  # Verifica clase01 sea igual a 1 o azar menor al valor ingresado en undersampling_value
        ).astype(int)
    #crea la columna clase peso para ayudar a calcular los pesos para el dataset de train de LGBM
    dataset['clase_peso'] = 1.0
    dataset.loc[(dataset['entrenamiento'] == 1) & (dataset['clase_ternaria']== 'BAJA+2'), 'clase_peso'] = 1.00001
    w_train = dataset.loc[(dataset['entrenamiento'] == 1), 'clase_peso'] # calculo de pesos para train
    #defino dataset de train de LGBM
    dtrain = lgb.Dataset(
                    data=dataset.loc[dataset['entrenamiento'] == 1, campos_buenos],
                    label=dataset.loc[dataset['entrenamiento'] == 1, "clase01"],
                    weight=w_train,
                    free_raw_data=False
                    )

    #calculo los pesos para el dataset de test y armo el dataset de test de LGBM
    dataset['clase_pesotest'] = 1.0
    dataset.loc[(dataset['foto_mes'] == mes_test) & (dataset['clase_ternaria']== 'BAJA+2'), 'clase_pesotest'] = 1.00001
    w_test =dataset.loc[(dataset['foto_mes'] == mes_test), 'clase_pesotest']
    dvalid = lgb.Dataset(
        data=dataset.loc[dataset["foto_mes"].isin(validation), campos_buenos],
        label=dataset.loc[dataset["foto_mes"].isin(validation), "clase01"],
        weight=w_test,
        free_raw_data=False
      )
    #los valores fueron tomados del experimiento de canarios asesinos z1601_CN_canaritos_asesinos
    param = {
        "objective": "binary",
        'metric':'custom',
        "first_metric_only": True,
        "boost_from_average": True,
        "feature_pre_filter": False,
        "verbosity": -100,
        "seed": valorsemilla,
        "max_depth": -1,
        "min_gain_to_split": 0.0,
        "lambda_l1": 0.0,
        "lambda_l2": 0.0,
        "max_bin": 31,
        "num_iterations": 9999,
        "force_row_wise": True,
        "learning_rate": 0.065,
        "feature_fraction": 1.0,
        "min_data_in_leaf": 260,
        "num_leaves": 60,
        "early_stopping_rounds": 200,
        "num_threads": 1
      }

    np.random.seed(valorsemilla)
    #entreno el modelo
    modelo = lgb.train (
      params=param,
      train_set=dtrain,
      valid_sets=[dvalid],
      feval=fganancia_lgbm_meseta
     )

    #obtengo las features importance
    importances = modelo.feature_importance()
    feature_names = campos_buenos
    importance_df = pd.DataFrame({'feature': feature_names, 'importance': importances})
    importance_df = importance_df.sort_values('importance', ascending=False)
    importance_df = importance_df.reset_index(drop=True)
    # Agrega la columna 'pos' para la posición o indice
    importance_df['pos'] = importance_df.index + 1
    # Lista de columnas a eliminar, usadas como auxiliares de calculo
    columnas_a_eliminar = ['clase01', 'clase_peso','clase_pesotest','entrenamiento']
    # Eliminar columnas especificadas
    dataset = dataset.drop(columns=columnas_a_eliminar)
    # Filtra las filas donde el nombre de la característica contiene "canarito"
    canarito_features = importance_df[importance_df['feature'].str.contains("canarito")]
    # Calcula la mediana y la desviación estándar de la columna 'pos' en este subconjunto "canarito"
    #calculo el umbral de corte
    for valordesvio in canaritos_desvios:
      umbral = canarito_features['pos'].median() + valordesvio * canarito_features['pos'].std()
      # Filtrar columnas útiles según el umbral y excluyo las que contienen "canarito"
      col_utiles = importance_df[
        (importance_df['pos'] < umbral) &
        (~importance_df['feature'].str.contains("canarito"))
      ]['feature'].tolist()
      # Agregar columnas adicionales como 'campitos'
      campitos = ["foto_mes", "clase_ternaria"]  # Reemplaza con los nombres reales de las columnas
      col_utiles = list(set(col_utiles + campitos))  # Usamos 'set' para obtener solo valores únicos
      # Determinar las columnas inútiles
      col_inutiles = set(dataset.columns) - set(col_utiles)
      # Eliminar columnas inutiles del dataset
      data = dataset
      data = data.drop(columns=col_inutiles)
      #guarda el dataset con las variables seleccionadas
      #dataset.to_csv(dataset_path + 'competencia02_FS.csv.gz', index=False, compression='gzip')
      #obtener ganancia del nuevo dataset con variables menos importantes eliminadas
      # Carga del dataset
      #dataset_file = 'competencia02_FS.csv.gz'# archivo de la competencia 02 a la que se le calculo previamente la clase ternaria
      #data = pd.read_csv(dataset_path + dataset_file,compression='gzip')
      data['clase_peso'] = 1.0
      data.loc[data['clase_ternaria'] == 'BAJA+2', 'clase_peso'] = 1.00002
      data.loc[data['clase_ternaria'] == 'BAJA+1', 'clase_peso'] = 1.00001
      data['clase_binaria1'] = 0
      data['clase_binaria2'] = 0
      data['clase_binaria1'] = np.where(data['clase_ternaria'] == 'BAJA+2', 1, 0)
      data['clase_binaria2'] = np.where(data['clase_ternaria'] == 'CONTINUA', 0, 1)
      train_data = data[data['foto_mes'] == mes_train]
      test_data = data[data['foto_mes'] == mes_test]
      X_train = train_data.drop(['clase_ternaria', 'clase_peso', 'clase_binaria1','clase_binaria2'], axis=1)
      y_train_binaria1 = train_data['clase_binaria1']
      y_train_binaria2 = train_data['clase_binaria2']
      w_train = train_data['clase_peso']
      X_test = test_data.drop(['clase_ternaria', 'clase_peso', 'clase_binaria1','clase_binaria2'], axis=1)
      y_test_binaria1 = test_data['clase_binaria1']
      y_test_class = test_data['clase_ternaria']
      w_test = test_data['clase_peso']
      train_data1 = lgb.Dataset(X_train, label=y_train_binaria1, weight=w_train)
      train_data2 = lgb.Dataset(X_train, label=y_train_binaria2, weight=w_train)
      params = {
        'objective': 'binary',
        'boosting_type': 'gbdt',
        'first_metric_only': True,
        'boost_from_average': True,
        'feature_pre_filter': False,
        'max_bin': 31,
        'num_leaves': 60,
        'learning_rate': 0.065,
        'min_data_in_leaf': 260,
        'feature_fraction': 1.0,
        "max_depth": -1,
        "min_gain_to_split": 0.0,
        "lambda_l1": 0.0,
        "lambda_l2": 0.0,
        "force_row_wise": True,
        "num_threads": 1,
        'seed': valorsemilla,
        'verbose': 0
      }

      train_data = lgb.Dataset(X_train,
                          label=y_train_binaria2,
                          weight=w_train)

      model = lgb.train(params,
                  train_data,
                  num_boost_round=100)

      y_pred_lgm = model.predict(X_test)
      def ganancia_prob(y_pred, y_true, prop = 1):
        ganancia = np.where(y_true == 1, ganancia_acierto, 0) - np.where(y_true == 0, costo_estimulo, 0)
        return ganancia[y_pred >= 0.025].sum() / prop

      resultados.loc[numero, 'Nro'] = numero
      resultados.loc[numero, 'Ratio'] = valorratio
      resultados.loc[numero, 'Desvio'] = valordesvio
      resultados.loc[numero, 'Variables importantes'] = len(col_utiles)
      resultados.loc[numero, 'Eliminadas'] = (155-len(col_utiles))*100/155
      resultados.loc[numero, 'Ganancia'] = ganancia_prob(y_pred_lgm, y_test_binaria1)
      resultados.loc[numero, 'Semilla'] = valorsemilla
      archivo = dataset_path +'colutiles'+str(numero)+'.txt'
      # col_utiles.to_csv(dataset_path + archivo, index=False)
      # Guardar la lista en un archivo de texto
      with open(archivo, "w") as file:
       for item in col_utiles:
          file.write(f"{item}\n")
      numero = numero +1
#guarda los resultados de las pruebas
resultados.to_csv(dataset_path + 'resultadoscanaritos.csv', index=False)
#Guardar el dataset con las columnas mas importantes para la maxima ganancia
orden = resultados.loc[resultados['Ganancia'].idxmax(), 'Nro']
# Leer el archivo y guardar cada línea en una lista
archivo =  dataset_path +'colutiles'+str(int(orden))+'.txt'
with open(archivo, "r") as file:
    mi_lista = [line.strip() for line in file]
dataset = dataset[mi_lista]
dataset.to_csv(dataset_path + 'competencia02FS.csv.gz', index=False, compression='gzip')

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped t

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped t

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con

...

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped t

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped t

/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[f"canarito{i+1}"] = np.random.uniform(0, 1, len(dataset))
/tmp/ipykernel_2261/2432658177.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.con